In [ ]:
var('z v u t tau')
function('P V')
var('r p', domain="integer")

In [ ]:
assumptions_dict = {
    P(u).diff(u)(u=tau) : 0
}

In [ ]:
maxima_calculus("algebraic: true")

In [ ]:
A.<Z> = AsymptoticRing('Z^QQ', SR, default_prec=3)
A2.<n> = AsymptoticRing('QQ^n * n^QQ', SR, default_prec=5)

In [ ]:
kernel = (v - z - z*(t-1)*(z*(P(v) - 1/v))^r)*(1 - z*(P(v) - 1/v)) - z^2*(P(v) - 1/v)

In [ ]:
# the analytic implicit function theorem is applicable:
kernel.factor().diff(v, 1).simplify_rational()(z=0, t=1, v=0)

In [ ]:
v_diff_1 = kernel.subs({v : V(z, t)}).diff(t, 1)(t=1).solve(V(z, t).diff(t, 1)(t=1))[0].subs({
    P(V(z, 1)) : 1/z
})
v_diff_1.simplify_rational().show()

In [ ]:
v_diff_2 = kernel.subs({v : V(z, t)}).diff(t, 2)(t=1).solve(V(z, t).diff(t, 2)(t=1))[0].subs({
    P(V(z, 1)) : 1/z
})
v_diff_2 = v_diff_2.subs(v_diff_1).simplify_rational().factor()
v_diff_2.show()

In [ ]:
assume(p, 'integer')
z_loc = 1/P(tau) * (1 - Z^-1)

def phi(u):
    return 1 if u == 0 else u * P(u)

V_rho_expansion = asymptotic_expansions.ImplicitExpansion(Z, phi=phi, tau=tau, precision=5)
excursions_rho_expansion = V_rho_expansion / z_loc

assume(tau > 0)
excursions_rho_expansion = excursions_rho_expansion.map_coefficients(lambda t: t.simplify_rational().subs(assumptions_dict).canonicalize_radical())
excursions_rho_expansion.show()

In [ ]:
var('a1 a2 a3')
excursions_stub_expansion = tau*P(tau) + a1*Z^(-1/2) + a2*Z^(-1) + a3*Z^(-3/2) + O(Z^-2)
excursions_stub_expansion.show()

In [ ]:
coefficients_dict = {
    a1: excursions_rho_expansion.monomial_coefficient(Z^(-1/2)),
    a2: excursions_rho_expansion.monomial_coefficient(Z^(-1)),
    a3: excursions_rho_expansion.monomial_coefficient(Z^(-3/2)),
}

In [ ]:
forget()
number_of_excursions = (p * excursions_stub_expansion)._singularity_analysis_('n', zeta=1/P(tau))
number_of_excursions.map_coefficients(lambda t: t.subs(coefficients_dict).simplify_rational().factor()).show()

In [ ]:
def function_expansion(f, x, x0, degree):
    return sum(f(u).diff(u, j)(u=x0).subs(assumptions_dict)/factorial(j) * (x - x0)^j for j in srange(degree+2))

P_V_expansion = function_expansion(P(u), excursions_stub_expansion*z_loc, tau, 4)
P_V_d1_expansion = function_expansion(P(u).diff(u), excursions_stub_expansion*z_loc, tau, 4)
P_V_d2_expansion = function_expansion(P(u).diff(u,2), excursions_stub_expansion*z_loc, tau, 4)

In [ ]:
var('V_z_1, P_d1_V')
v_diff_1_func = fast_callable((v_diff_1.rhs() / z).subs({
    P(u).diff(u)(u=V(z,1)) : P_d1_V,
}).subs({
    V(z,1) : V_z_1
}).simplify_rational(), vars=[V_z_1, P_d1_V, z, r])
expectation_expansion = v_diff_1_func(excursions_stub_expansion*z_loc, P_V_d1_expansion, z_loc, r)
expectation_expansion = expectation_expansion.map_coefficients(lambda t: t.canonicalize_radical())

In [ ]:
expectation_unnormalized = (p * expectation_expansion)._singularity_analysis_(n, zeta=1/P(tau))

In [ ]:
from utilities import group_by_denominator
var('c')
assume(r, 'integer')
expectation_normalized = (expectation_unnormalized / number_of_excursions).map_coefficients(lambda t: t.simplify_rational())
expectation_normalized = expectation_normalized.map_coefficients(lambda t: t.subs(coefficients_dict).subs(
    {P(tau): c/tau, (-c + 1)^r : (-1)^r * (c - 1)^r}).simplify_rational().factor())
expectation_normalized.map_coefficients(group_by_denominator).show()

In [ ]:
# Example: Dyck paths -- P(u) = 1/u + u

expectation_normalized.map_coefficients(lambda t: t.subs({
    P(tau).diff(tau,2)(tau=1): 2,
    P(tau).diff(tau,3)(tau=1): -6,
    P(1): 2,
    tau: 1,
    p: 2,
    c: 2,
}).canonicalize_radical().factor()).show()

In [ ]:
var('V_z_1, P_d1_V, P_d2_V')
v_diff_2_func = fast_callable((v_diff_2.rhs() / z).subs({
    P(u).diff(u)(u=V(z,1)) : P_d1_V,
    P(u).diff(u, 2)(u=V(z,1)) : P_d2_V,
}).subs({
    V(z,1) : V_z_1
}).simplify_rational(), vars=[V_z_1, P_d1_V, P_d2_V, z, r])
fmom2_expansion = v_diff_2_func(excursions_stub_expansion * z_loc, P_V_d1_expansion, P_V_d2_expansion, z_loc, r)
fmom2_expansion = fmom2_expansion.map_coefficients(lambda t: t.canonicalize_radical())

In [ ]:
fmom2_unnormalized = (p * fmom2_expansion)._singularity_analysis_(n, zeta=1/P(tau))
fmom2_normalized = (fmom2_unnormalized / number_of_excursions).map_coefficients(lambda t: t.simplify_rational())

In [ ]:
from utilities import group_by_denominator
assume(c>0)
variance_asy = fmom2_normalized + expectation_normalized - expectation_normalized^2
variance_asy = variance_asy.map_coefficients(lambda t: t.subs(coefficients_dict).canonicalize_radical())
variance_asy.map_coefficients(lambda t: 
    t.subs({P(tau): c/tau}).simplify_rational().subs(
        {(1-c)^(2*r): (c-1)^(2*r)}
    ).simplify_rational()).map_coefficients(group_by_denominator).show()

In [ ]:
# Example: Dyck paths -- P(u) = 1/u + u
assume(r, 'integer')
variance_asy.map_coefficients(lambda t: t.subs({
    P(tau).diff(tau,2)(tau=1): 2,
    P(tau).diff(tau,3)(tau=1): -6,
    P(1): 2,
    tau: 1,
    p: 2,
    c: 2,
}).canonicalize_radical()).show()

## Special case: $\mathcal{S} = \{-1, 1\}$

In [ ]:
P(u) = 1/u + u

In [ ]:
kernel = (v - z - z*(t-1)*(z*(P(v) - 1/v))^r)*(1 - z*(P(v) - 1/v)) - z^2*(P(v) - 1/v)

In [ ]:
[v_sol] = list(eq.rhs() for eq in solve(v == z*v*P(v), v) if eq.rhs().limit(z=0) == 0)
v_sol.show()

In [ ]:
# substitution: z^2 = u/(1 + u)^2
(v_sol / z).subs({z : sqrt(u)/(1+u)}).simplify_rational().subs({
    sqrt((u^2 - 2*u + 1)/(u^2 + 2*u + 1)) : (1-u)/(1+u)
}).simplify_rational().show()

In [ ]:
F_r_func = fast_callable(v_sol/z, vars=[z])
number_of_excursions = A2.coefficients_of_generating_function(lambda z: F_r_func(sqrt(z)), singularities=[1/4], precision=6)
number_of_excursions.show()

In [ ]:
v_diff_1 = kernel.subs({v : V(z,t)}).diff(t,1)(t=1).solve(V(z,t).diff(t,1)(t=1))[0].subs({
    V(z,1) : v_sol
})
v_diff_1.simplify_rational().factor().show()

In [ ]:
# substitution: z^2 = u/(1 + u)^2
(v_diff_1.rhs() / z).subs({z : sqrt(u)/(1+u)}).simplify_rational().subs({
    sqrt((u^2 - 2*u + 1)/(u^2 + 2*u + 1)) : (1-u)/(1+u),
    1/sqrt((u^2 - 2*u + 1)/(u^2 + 2*u + 1)) : (1+u)/(1-u)
}).factor().show()

In [ ]:
F_r_diff1_func = fast_callable(v_diff_1.rhs()/z, vars=[z,r])
expectation_unnormalized = A2.coefficients_of_generating_function(lambda z: F_r_diff1_func(sqrt(z), r), singularities=[1/4], precision=6)
expectation_unnormalized = expectation_unnormalized.map_coefficients(lambda t: t.canonicalize_radical())
expectation_normalized = expectation_unnormalized / number_of_excursions
expectation_normalized.map_coefficients(lambda t: t.factor()).show()

In [ ]:
v_diff_2 = kernel.subs({v : V(z,t)}).diff(t,2)(t=1).solve(V(z,t).diff(t,2)(t=1))[0].subs({
    V(z,1) : v_sol
})
v_diff_2 = v_diff_2.subs(v_diff_1).simplify_rational().factor()
v_diff_2.show()

In [ ]:
# substitution: z^2 = u/(1 + u)^2
(v_diff_2.rhs() / z).subs({z : sqrt(u)/(1+u)}).simplify_rational().subs({
    sqrt((u^2 - 2*u + 1)/(u^2 + 2*u + 1)) : (1-u)/(1+u),
    1/sqrt((u^2 - 2*u + 1)/(u^2 + 2*u + 1)) : (1+u)/(1-u)
}).factor().show()

In [ ]:
F_r_diff2_func = fast_callable(v_diff_2.rhs()/z, vars=[z,r])
fmom2_unnormalized = A2.coefficients_of_generating_function(lambda z: F_r_diff2_func(sqrt(z), r), singularities=[1/4], precision=5)
fmom2_unnormalized = fmom2_unnormalized.map_coefficients(lambda t: t.canonicalize_radical())
fmom2_normalized = fmom2_unnormalized / number_of_excursions
variance_asy = fmom2_normalized + expectation_normalized - expectation_normalized^2
variance_asy.map_coefficients(lambda t: t.factor()).show()

In [ ]:
variance_asy_simplified = ((1/2^(r+1) - (r^2 - 2*r + 3)/2^(2*r+3)) * n 
                           - ((r^2 - 3*r - 4)/2^(r+3) - (3*r^4 - 20*r^3 + 29*r^2 - 10*r - 14)/2^(2*r+5)) 
                           + O(n^(-1/2)))

(variance_asy_simplified - variance_asy).exact_part().map_coefficients(lambda t: t.canonicalize_radical()).is_zero()

In [ ]:
variance_asy_simplified.show()